In [1]:
import pandas as pd
import numpy as np
# from bidi.algorithm import get_display # the script can get a string as a parameter or read text from stdin
from wordcloud import WordCloud, STOPWORDS # to perform Exploratory Data Analysis
import matplotlib.pyplot as plt
import arabic_reshaper #Reconstruct Arabic sentences to be used in applications that don't support Arabic script.
from nltk.stem.isri import ISRIStemmer
from sklearn.feature_extraction.text import CountVectorizer
# Arabic stopword
from nltk.corpus import stopwords
import nltk #For working with human languge
# nltk.download('stopwords')
from nltk.tokenize import word_tokenize
import re #to provides regular expression matching operations similar to those found in Perl.
import string
import sys
import argparse
import emoji
from nltk.stem.isri import ISRIStemmer #Light Arabic stemming algorithm  
import itertools #To provide simlier feature based on iterartion
from sklearn import preprocessing
#from dsaraby import DSAraby 
#ds = DSAraby()
#from tashaphyne.stemming import ArabicLightStemmer

import warnings
warnings.filterwarnings('ignore')


Bad key text.latex.preview in file C:\Users\hp\anaconda3\lib\site-packages\matplotlib\mpl-data\stylelib\_classic_test.mplstyle, line 123 ('text.latex.preview : False')
You probably need to get an updated matplotlibrc file from
https://github.com/matplotlib/matplotlib/blob/v3.5.0/matplotlibrc.template
or from the matplotlib source distribution

Bad key mathtext.fallback_to_cm in file C:\Users\hp\anaconda3\lib\site-packages\matplotlib\mpl-data\stylelib\_classic_test.mplstyle, line 155 ('mathtext.fallback_to_cm : True  # When True, use symbols from the Computer Modern')
You probably need to get an updated matplotlibrc file from
https://github.com/matplotlib/matplotlib/blob/v3.5.0/matplotlibrc.template
or from the matplotlib source distribution

Bad key savefig.jpeg_quality in file C:\Users\hp\anaconda3\lib\site-packages\matplotlib\mpl-data\stylelib\_classic_test.mplstyle, line 418 ('savefig.jpeg_quality: 95       # when a jpeg is saved, the default quality parameter.')
You probably need 

In [ ]:
#! pip install arabicstopwords
#nltk.download('stopwords')
#! pip install emoji
# ! pip install transliterate

In [2]:
df = pd.read_csv('RES1.csv') #'arabic_dataset_classifiction.csv')
df

polarity                                               text  \
0           -1  اولا: المنيو تغير الشورما اصبحت اعتياديه بأختف...   
1           -1  من محلات الشاورما ذات الشعبيه لتميز الصلصات ال...   
2            1  دجاج طازج يحضر امامك على الطلب لا يقوم باعدة ا...   
3            1  فكما تعرف أستراليا بالكنغر والكوالا. فإنها تعر...   
4           -1  إسمحو لي أن أقيم مطعم هاشم بصفتي فلسطيني عشت ف...   
...        ...                                                ...   
8359         1  أتمنى تعملو بطاقات خاصة أو ذهبية للعملاء الدائ...   
8360         1  المشويات عندهم اطيب مشويات اكلتها بحياتي والاس...   
8361         1  المطعم ممتاز للغايه ، من ناحيه تجهيزات المطعم ...   
8362        -1  جينا عندهم الساعة 10 بالليل مافى احد اتبرع يشو...   
8363         1  اذا كان اللي بالشارع التجاري اوووه ماشاء الله ...   

      restaurant_id  user_id  
0               296      423  
1               296      423  
2              5027    39580  
3               642      444  
4               434     2191  
...             ...      ...  
8359           4990    39151  
8360           4990    34712  
8361           1050     2284  
8362           3243     4598  
8363           1458    26736  

[8364 rows x 4 columns]

In [3]:
df.shape

(8364, 4)

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8364 entries, 0 to 8363
Data columns (total 4 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   polarity       8364 non-null   int64 
 1   text           8364 non-null   object
 2   restaurant_id  8364 non-null   int64 
 3   user_id        8364 non-null   int64 
dtypes: int64(3), object(1)
memory usage: 261.5+ KB


In [5]:
df.isnull().sum()

polarity         0
text             0
restaurant_id    0
user_id          0
dtype: int64

In [6]:
df.polarity.value_counts()

 1    5946
-1    2418
Name: polarity, dtype: int64

In [7]:
all_words = []
for item in df.text:
    w = nltk.tokenize.word_tokenize(item)
    all_words += w
len(all_words)

355092

- Find The 30 Most Common Words in text culomn

In [8]:
# Instantiate CountVectorizer
cv = CountVectorizer()
# Fit the text with CountVectorizer
bow_restaurant = cv.fit(df.text)
bow_restaurant_t = bow_restaurant.transform(df.text)
# Define dataframe that contains the frequency of words in each text
count_vect_df = pd.DataFrame(bow_restaurant_t.todense(), columns=bow_restaurant.get_feature_names())

In [9]:
# Define dataframe that contains the sum of words frequency 
sum_df = pd.DataFrame(np.sum(bow_restaurant_t.todense(),axis=0), columns=cv.get_feature_names())

# Sort by the frequency of words of first 20 common words
sum_df.sort_values(by=0, ascending=False, axis=1).iloc[:,:30]

من    في  المطعم   جدا    ما   على    مع    بس  مطعم   كان  ...  ريال  \
0  7001  5179    3526  3176  2549  2505  1792  1689  1660  1608  ...   937   

    كل   عن   شي  ممتاز  كانت  المطاعم   له  انا   هو  
0  924  922  914    840   839      838  818  788  778  

[1 rows x 30 columns]

## Pre-processing
- Data cleaning
 - Drop the duplicate values.
 - Remove stop words.
 - Remove the stop words.
 - Remove punctuations.
 - Normalize arabic text.
 - Remove emojis.
 - Remove repeating char.
 - Stemming.
 - ProcessPost for applying all functions.
 

### drop the duplicate values

In [10]:
# The number of duplicates 
print("The number of duplicates: ", df.duplicated(subset=None, keep='first').sum())
print("The number of after drop duplicates: ", df.drop_duplicates(inplace=True))
# the number of non-duplicates 
print("The number rows of non-duplicates: ", (~df.duplicated()).sum())

The number of duplicates:  36
The number of after drop duplicates:  None
The number rows of non-duplicates:  8328


- Collect all the word tokens in the text column: to compute how many tokens in the data, we have (355092) tokens.
- Then we have used one of the famous ways called (word cloud) to visualize the text data, to focused on words according to it's repeat times, in this steps 

In [11]:
def emoji_counter(sentence):
    return emoji.emoji_count(sentence)

df['word_count'] = df['text'].apply(lambda x: len(str(x).split(" ")))
df['char_count'] = df['text'].str.len() ## this also includes spaces
stop = stopwords.words('arabic')
df['stopwords'] = df['text'].apply(lambda x: len([x for x in x.split() if x in stop]))
df['emoji_count'] = df['text'].apply(lambda x: emoji_counter(x))
df = df.sort_values(by='word_count',ascending=[0])
df.head(10)

polarity                                               text  \
2245         1  زيراتي للمطاعم عادتآ تكون بتخطيط مسبق لكن الزي...   
102          1  المطعم يستخدم نظام البوصة, حيث أن أغلب وجباته ...   
4903        -1  بسم الله  \n وصلى الله وسلم على رسول الله \n  ...   
6232        -1  هذ التقييم لفرع التحلية \n  \n المكسيكين ضيافت...   
4335         1  السلام عليكم  \n  \n اليوم قررت اني اخذ العيال...   
5117         1  السلام عليكم  \n  \n تقييمي راح يكون كالاتي  \...   
5060        -1  اليوم حبيت أكل شي صيني \n فجلست افكر بكم محل \...   
6233         1  مطعم الشيكو \n من مدة ما تكلمت عن المطاعم \n  ...   
6309         1  السلام عليكم،، \n بالنسبة لي ، فزياراتي متكررة...   
6163        -1  بالبداية لم أعرف كيف أو ماذا سأكتب عن هذ المطع...   

      restaurant_id  user_id  word_count  char_count  stopwords  emoji_count  
2245           2038     3690         912        4742        105            0  
102              68     5231         890        4246         58            0  
4903           1986     4446         846        4250        128            0  
6232           1956     3690         796        4118        101            0  
4335           2108     4446         746        3638        110            0  
5117           1350     3690         673        3578        102            0  
5060           1981     4614         621        2930        102            0  
6233           1956    38204         577        2457         74            0  
6309             41     4295         573        2737         89            0  
6163           2151     3690         552        3028         99            0

### Remove the unwanted words (stop words) 

In [12]:
all_stopwords = stopwords.words('arabic')
all_stopwords

['إذ',
 'إذا',
 'إذما',
 'إذن',
 'أف',
 'أقل',
 'أكثر',
 'ألا',
 'إلا',
 'التي',
 'الذي',
 'الذين',
 'اللاتي',
 'اللائي',
 'اللتان',
 'اللتيا',
 'اللتين',
 'اللذان',
 'اللذين',
 'اللواتي',
 'إلى',
 'إليك',
 'إليكم',
 'إليكما',
 'إليكن',
 'أم',
 'أما',
 'أما',
 'إما',
 'أن',
 'إن',
 'إنا',
 'أنا',
 'أنت',
 'أنتم',
 'أنتما',
 'أنتن',
 'إنما',
 'إنه',
 'أنى',
 'أنى',
 'آه',
 'آها',
 'أو',
 'أولاء',
 'أولئك',
 'أوه',
 'آي',
 'أي',
 'أيها',
 'إي',
 'أين',
 'أين',
 'أينما',
 'إيه',
 'بخ',
 'بس',
 'بعد',
 'بعض',
 'بك',
 'بكم',
 'بكم',
 'بكما',
 'بكن',
 'بل',
 'بلى',
 'بما',
 'بماذا',
 'بمن',
 'بنا',
 'به',
 'بها',
 'بهم',
 'بهما',
 'بهن',
 'بي',
 'بين',
 'بيد',
 'تلك',
 'تلكم',
 'تلكما',
 'ته',
 'تي',
 'تين',
 'تينك',
 'ثم',
 'ثمة',
 'حاشا',
 'حبذا',
 'حتى',
 'حيث',
 'حيثما',
 'حين',
 'خلا',
 'دون',
 'ذا',
 'ذات',
 'ذاك',
 'ذان',
 'ذانك',
 'ذلك',
 'ذلكم',
 'ذلكما',
 'ذلكن',
 'ذه',
 'ذو',
 'ذوا',
 'ذواتا',
 'ذواتي',
 'ذي',
 'ذين',
 'ذينك',
 'ريث',
 'سوف',
 'سوى',
 'شتان',
 'عدا',
 'عسى',
 'عل'

In [13]:
print(len(all_stopwords))

754


In [14]:
print(type(all_stopwords))

<class 'list'>


In [15]:
listToStr = ' '.join([str(elem) for elem in all_stopwords])
listToStr

'إذ إذا إذما إذن أف أقل أكثر ألا إلا التي الذي الذين اللاتي اللائي اللتان اللتيا اللتين اللذان اللذين اللواتي إلى إليك إليكم إليكما إليكن أم أما أما إما أن إن إنا أنا أنت أنتم أنتما أنتن إنما إنه أنى أنى آه آها أو أولاء أولئك أوه آي أي أيها إي أين أين أينما إيه بخ بس بعد بعض بك بكم بكم بكما بكن بل بلى بما بماذا بمن بنا به بها بهم بهما بهن بي بين بيد تلك تلكم تلكما ته تي تين تينك ثم ثمة حاشا حبذا حتى حيث حيثما حين خلا دون ذا ذات ذاك ذان ذانك ذلك ذلكم ذلكما ذلكن ذه ذو ذوا ذواتا ذواتي ذي ذين ذينك ريث سوف سوى شتان عدا عسى عل على عليك عليه عما عن عند غير فإذا فإن فلا فمن في فيم فيما فيه فيها قد كأن كأنما كأي كأين كذا كذلك كل كلا كلاهما كلتا كلما كليكما كليهما كم كم كما كي كيت كيف كيفما لا لاسيما لدى لست لستم لستما لستن لسن لسنا لعل لك لكم لكما لكن لكنما لكي لكيلا لم لما لن لنا له لها لهم لهما لهن لو لولا لوما لي لئن ليت ليس ليسا ليست ليستا ليسوا ما ماذا متى مذ مع مما ممن من منه منها منذ مه مهما نحن نحو نعم ها هاتان هاته هاتي هاتين هاك هاهنا هذا هذان هذه هذي هذين هكذا هل هلا هم هما هن هنا هن

In [16]:
df.text[15]

'أنا شخصياً أحب مطاعم كنتاكي KFC \n خاصةً في الأردن  \n حيث أنها تتميز بالجودة ، الخدمة الجيدة \n النظافة ، وكذلك الطعم الرهيييييب'

In [17]:
def remove_stop_words(text):
    all_stopwords = list(set(stopwords.words("arabic"))) + pd.read_csv('Stopwords.txt').iloc[:,0].values.tolist()
    needed_words = []
    words = nltk.tokenize.word_tokenize(text)
    for w in words:
        if w not in all_stopwords and len(w) >= 2:
            needed_words.append(w)
            # join the list of  words without stop words, as shown below:
    filtered_sentence = " ".join(needed_words)# " ".join(needed_words)
    return filtered_sentence # " ".join(needed_words)

In [18]:
df["cleaned_text"] = df["text"].apply(lambda text : remove_stop_words(text))
df.cleaned_text[15]

'شخصياً أحب مطاعم كنتاكي KFC خاصةً الأردن أنها تتميز بالجودة الخدمة الجيدة النظافة وكذلك الطعم الرهيييييب'

In [22]:
tt =df['cleaned_text']
tt = ' '.join([str(elem) for elem in tt])
tt

'زيراتي للمطاعم عادتآ بتخطيط مسبق الزيارتين زرتهم للمطعم كانو خارج التخطيط تمامآ خصوصآ اني معزوم عائله صينيه تعشق المكان لان العئله المالكه والعامله مسلمه وتتبع الذبح والطبخ الحلال المكان المطعم حجمه صغير جدآ ومقسم لقسمين القسم الأول لكل هب ودب ومزود طاولات تقريبآ الوحده فيهم تاخذ اشخاص القسم هذ بالذات يحسسك انك بالصين مباشرتآ فالتلفزيون المعلق بالزاويه يعرضلك فلم صيني ترجمة دبلجة المطبخ المفتوح جزئيآ المكان ويزود المتعشي بسماع النقاش الكومدي الشف والطاقم وليتك تفهم شي ههه القسم عباره غرفتين مغلقتين معزولات تمامآ القسم الأول والمطبخ الغريب انك اذ تبي توصلهم لازم تدخل المطبخ وتعدي طاقم المطبخ والله يعين السلام والمجاملات طبعآ القسم هذ لازمله حجز مسبق وعدد اكبر لانه ياخذ اشخاص القائمة ماقدرت اخذ نضره قائمتهم اني كنت معزوم بالزيارتين الأولى بالغرفة المغلقه والثانيه بالمنطقة المفتوحه لاكني قدرت استنبط الثيم القائمه شعبي بحت شدة تراثية الأطباق فماكنت اعرف منهم طبق طبقين والثيم يشرح حرفيآ اسم المطعم Old mandarin الاطباق كراعين كعب البقر الحمل  الخ واعتبره مثال بسيط تراثية الاطباق الاطباق بال

### Remove punctuations 

In [19]:
df.text[40]

'زرت هذا المطعم بفرع الخبر الكورنيش، طلبت برجر لا أذكر إسمه لكنه كان جيد الطعم وثقيل نوعاً ما من الدسم، البطاطس عادي لم يكن مميز عن غيره لكنه كان جيد. \n  \n ما ساءني بصراحة هو الموظفين لم يكونوا باللطافة المطلوبة في مطعم مثل هذا النوع، فلا أدري ماهي النوع من الجمود. لم يكن هناك أي إبتسامة من الموظفين. \n  \n الشيء الآخر وهو كثرة الذباب في المكان ورائحة الزيت السيئة، رائحة الزيت غالبا أجدها في فدركرز وجوني روكيت لكن الذباب كان مزعج جداً،، لدرجة أن الذباب يقف على الطاولة أمامي بشكل متكرر وقد صورت بعضها تجدونها في الصور. \n  \n مطعم جيد، لكن لا أراه مميز عن جوني روكيت أو فدركز. وكلها غير صحية بكثرة الزيت والشحم.'

In [20]:
arabic_punctuations = '''`÷×؛<>_()*&^%][ـ،/:"؟.,'{}~¦+|!”…“–ـ'''
english_punctuations = string.punctuation
punctuations_list = arabic_punctuations + english_punctuations

def remove_punctuations(text):
    translator = str.maketrans('', '', punctuations_list)
    return text.translate(translator)

In [21]:
df["cleaned_text"] = df["cleaned_text"].apply(lambda text : remove_punctuations(text))
df.cleaned_text[40]

'زرت المطعم بفرع الخبر الكورنيش طلبت برجر أذكر إسمه جيد الطعم وثقيل نوعاً الدسم البطاطس عادي يكن مميز غيره جيد ساءني بصراحة الموظفين يكونوا باللطافة المطلوبة مطعم النوع أدري ماهي النوع الجمود يكن إبتسامة الموظفين الشيء الآخر كثرة الذباب المكان ورائحة الزيت السيئة رائحة الزيت أجدها فدركرز وجوني روكيت الذباب مزعج جداً لدرجة الذباب يقف الطاولة أمامي متكرر صورت بعضها تجدونها الصور مطعم جيد أراه مميز جوني روكيت فدركز وكلها صحية بكثرة الزيت والشحم'

In [23]:
tt =df['cleaned_text']
tt = ' '.join([str(elem) for elem in tt])
tt

'زيراتي للمطاعم عادتآ بتخطيط مسبق الزيارتين زرتهم للمطعم كانو خارج التخطيط تمامآ خصوصآ اني معزوم عائله صينيه تعشق المكان لان العئله المالكه والعامله مسلمه وتتبع الذبح والطبخ الحلال المكان المطعم حجمه صغير جدآ ومقسم لقسمين القسم الأول لكل هب ودب ومزود طاولات تقريبآ الوحده فيهم تاخذ اشخاص القسم هذ بالذات يحسسك انك بالصين مباشرتآ فالتلفزيون المعلق بالزاويه يعرضلك فلم صيني ترجمة دبلجة المطبخ المفتوح جزئيآ المكان ويزود المتعشي بسماع النقاش الكومدي الشف والطاقم وليتك تفهم شي ههه القسم عباره غرفتين مغلقتين معزولات تمامآ القسم الأول والمطبخ الغريب انك اذ تبي توصلهم لازم تدخل المطبخ وتعدي طاقم المطبخ والله يعين السلام والمجاملات طبعآ القسم هذ لازمله حجز مسبق وعدد اكبر لانه ياخذ اشخاص القائمة ماقدرت اخذ نضره قائمتهم اني كنت معزوم بالزيارتين الأولى بالغرفة المغلقه والثانيه بالمنطقة المفتوحه لاكني قدرت استنبط الثيم القائمه شعبي بحت شدة تراثية الأطباق فماكنت اعرف منهم طبق طبقين والثيم يشرح حرفيآ اسم المطعم Old mandarin الاطباق كراعين كعب البقر الحمل  الخ واعتبره مثال بسيط تراثية الاطباق الاطباق بال

### Remove emojis 

In [24]:
df.text[5673]

'😜😜عاادي😜😜'

In [25]:
# https://gist.github.com/bfeldman89/fb25ddb63bdaa6de6ab7ac946acde96f#file-emojis-csv
# https://github.com/motazsaad/process-arabic-text/blob/master/clean_arabic_text.py
def remove_emoji(text):
    regrex_pattern = re.compile(pattern = "["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002500-\U00002BEF"  # chinese char
        u"\U00002702-\U000027B0"
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u"\U00010000-\U0010ffff"
        u"\u2640-\u2642"
        u"\u2600-\u2B55"
        u"\u200d"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\ufe0f"  # dingbats
        u"\u3030"                        
         "]+", flags = re.UNICODE) # VERBOSE
    return regrex_pattern.sub(r'',text)

df["cleaned_text"] = df["cleaned_text"].apply(lambda text : remove_emoji(text))
df.cleaned_text[5673]

'عاادي'

In [26]:
tt =df['cleaned_text']
tt = ' '.join([str(elem) for elem in tt])
tt

'زيراتي للمطاعم عادتآ بتخطيط مسبق الزيارتين زرتهم للمطعم كانو خارج التخطيط تمامآ خصوصآ اني معزوم عائله صينيه تعشق المكان لان العئله المالكه والعامله مسلمه وتتبع الذبح والطبخ الحلال المكان المطعم حجمه صغير جدآ ومقسم لقسمين القسم الأول لكل هب ودب ومزود طاولات تقريبآ الوحده فيهم تاخذ اشخاص القسم هذ بالذات يحسسك انك بالصين مباشرتآ فالتلفزيون المعلق بالزاويه يعرضلك فلم صيني ترجمة دبلجة المطبخ المفتوح جزئيآ المكان ويزود المتعشي بسماع النقاش الكومدي الشف والطاقم وليتك تفهم شي ههه القسم عباره غرفتين مغلقتين معزولات تمامآ القسم الأول والمطبخ الغريب انك اذ تبي توصلهم لازم تدخل المطبخ وتعدي طاقم المطبخ والله يعين السلام والمجاملات طبعآ القسم هذ لازمله حجز مسبق وعدد اكبر لانه ياخذ اشخاص القائمة ماقدرت اخذ نضره قائمتهم اني كنت معزوم بالزيارتين الأولى بالغرفة المغلقه والثانيه بالمنطقة المفتوحه لاكني قدرت استنبط الثيم القائمه شعبي بحت شدة تراثية الأطباق فماكنت اعرف منهم طبق طبقين والثيم يشرح حرفيآ اسم المطعم Old mandarin الاطباق كراعين كعب البقر الحمل  الخ واعتبره مثال بسيط تراثية الاطباق الاطباق بال

### Normalize arabic text 

In [27]:
df.text[8363]

'اذا كان اللي بالشارع التجاري اوووه ماشاء الله والله انه خبال'

In [28]:
def noramlize(text):
    text = re.sub(r"[إأٱآا]", "ا", text)
    text = re.sub(r"ى", "ي", text)
    text = re.sub(r"ؤ", "ء", text)
    text = re.sub(r"ئ", "ء", text)
    text = re.sub("ة", "ه", text)
    text = re.sub("گ", "ك", text)
    text = re.sub(r'[^ا-ي ]', "", text)

    noise = re.compile(""" ّ    | # Tashdid
                             َ    | # Fatha
                             ً    | # Tanwin Fath
                             ُ    | # Damma
                             ٌ    | # Tanwin Damm
                             ِ    | # Kasra
                             ٍ    | # Tanwin Kasr
                             ْ    | # Sukun
                             ـ     # Tatwil/Kashida
                         """, re.VERBOSE)
    text = re.sub(noise, '', text)
    return text

df["cleaned_text"] = df["cleaned_text"].apply(lambda text : noramlize(text))
df.text[8363]

'اذا كان اللي بالشارع التجاري اوووه ماشاء الله والله انه خبال'

In [ ]:
tt =df['cleaned_text']
tt = ' '.join([str(elem) for elem in tt])
tt

### Remove repeating char 

In [30]:
df.text[2824]

'لذييييييذ'

In [31]:
def remove_repeating_char(text):
    return re.sub(r'(.)\1+', r'\1', text)

df["cleaned_text"] = df["cleaned_text"].apply(lambda text : remove_repeating_char(text))
df.cleaned_text[2824]

'لذيذ'

In [ ]:
tt =df['cleaned_text']
tt = ' '.join([str(elem) for elem in tt])
tt

## Stemming
### ISRIStemmer :

In [32]:
def stemming(text):
    st = ISRIStemmer()
    stemmed_words = []
    words = word_tokenize(text)
    for w in words:
        stemmed_words.append(st.stem(w))
    stemmed_sentence = " ".join(stemmed_words)
    return stemmed_sentence

df["cleaned_text"] = df["cleaned_text"].apply(lambda text : stemming(text))

In [ ]:
tt =df['cleaned_text']
tt = ' '.join([str(elem) for elem in tt])
tt

###  ProcessPost for applying all functions

In [33]:
def processPost(text): 

    #Replace @username with empty string
    #text = re.sub('@[^\s]+', ' ', text)
    
    # remove extra whitespace
    text = re.sub('\s+', ' ', text)
    
    # Remove numbers
    text = re.sub("\d+", " ", text)
    
    #Convert www.* or https?://* to " "
    text = re.sub('((www\.[^\s]+)|(https?://[^\s]+))',' ',text, flags=re.MULTILINE)
    text = re.sub(r'^http?:W.[\r\n]',' ', text, flags=re.MULTILINE)
    
    #Replace #word with word
    text = re.sub(r'#([^\s]+)', r'\1', text)
    
    text = re.sub('[A-Za-z]+',' ',text)
    text = re.sub(r'\\u[A-Za-z0-9\\]+',' ',text)
    
    return text

df["cleaned_text"] = df["cleaned_text"].apply(lambda text : processPost(text))
tt =df['cleaned_text']
tt = ' '.join([str(elem) for elem in tt])
tt

'زير طعم عدت خطط سبق زير زرت طعم كنو خرج خطط تما خصص اني عزم عله صين عشق كان لان عله الك عمل سلم تبع ذبح طبخ حلل كان طعم حجم صغر جدا قسم قسم قسم اول لكل هب ودب زود طول قرب وحد يهم تخذ شخص قسم هذ ذات يحس انك صين بشر فالتلفزي علق زوي عرضل فلم صين رجم دبلج طبخ فتح جزا كان يزد تعش سمع نقش كومد لشف طقم ولت فهم شي ه قسم عبر غرف غلق عزل تما قسم اول طبخ غرب انك اذ تبي وصل لزم دخل طبخ تعد طقم طبخ وله يعن سلم جمل طبع قسم هذ زمل حجز سبق وعد كبر لنه يخذ شخص قمه اقدر اخذ نضر قمت اني كنت عزم زير اول غرف غلق ثني طقه فتح لاك قدر نبط ثيم قمه شعب بحت شده رثه طبق فمك عرف نهم طبق طبق ثيم شرح حرف اسم طعم طبق كرع كعب بقر حمل الخ عبر ثال بسط رثه طبق طبق طول تقم نسب جرب اول بعض جرب سبق لخر رقه وفو شعر عبر وفو خير فضل طبق قدم زير فقد تبل مرق حمض زعج رقه ضلع الض طبق هذ مايجيبونه ورح سيل لعب حوط كان خصص حطه قدم طول تخل بخر خرج طبق شكل شكل صبع سبب يند تعل طبق جرب كطبق شعب رقه كثف ومل قريفنس كثف مرق لزج دسم ضلع زوج طعم بهر تخل عبر سان تعط طعم يفل راع لحم طبخ لمد نضج تذب لحم قضم دمبلنقز نتو حشو لحم الض كنو نوع بخر 

In [34]:
def prepare(text):
    text = remove_stop_words(text)
    text = remove_punctuations(text)
    #text = "".join([w for w in words if w not in string.punctuation])
    txet = noramlize(text)
    text = remove_emoji(text)
    text = stemming(text)
    tokens = word_tokenize(text)
    text = remove_repeating_char(text)
    text = processPost(text)
    # text = ' '.join([word for word in tokens if word not in stop_words])
    return text

df["cleaned_text"] = df["cleaned_text"].apply(lambda text : prepare(text))

In [35]:
# Instantiate CountVectorizer
cv = CountVectorizer()
# Fit the text with CountVectorizer
bow_restaurant = cv.fit(df.cleaned_text)
bow_restaurant_t = bow_restaurant.transform(df.cleaned_text)
# Define dataframe that contains the frequency of words in each text
count_vect_df = pd.DataFrame(bow_restaurant_t.todense(), columns=bow_restaurant.get_feature_names())

In [36]:
# Define dataframe that contains the sum of words frequency 
sum_df = pd.DataFrame(np.sum(bow_restaurant_t.todense(),axis=0), columns=cv.get_feature_names())

# Sort by the frequency of words of first 20 common words
sum_df.sort_values(by=0, ascending=False, axis=1).iloc[:,:30]

طعم   اكل   طلب   سعر   جرب   مره    لذ   فضل   خدم    دج  ...   عجب  \
0  9669  3116  2951  2743  2468  1909  1894  1679  1660  1594  ...  1083   

    جلس   كثر   صرح  شكل  عدي  تاز  نصح  يتز  رجر  
0  1080  1059  1026  964  932  928  894  884  862  

[1 rows x 30 columns]

In [37]:
df.to_csv("Final_RES1.csv", encoding="utf-8")